##Import data & libraries

In [88]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
import random
#import missingno as msno
#from google.colab import data_table
#from tabulate import tabulate
import scipy.stats as st
import matplotlib.patches as mpl_patches
import warnings
warnings.filterwarnings("ignore")
from scipy.stats import describe
import matplotlib.cm as cm
import matplotlib.lines as mlines
from scipy.stats import pearsonr
# !pip install powerbiclient
from tqdm import tqdm

### Funciones para explorar correlaciones

In [72]:
def heatmap(df):
    plt.figure(figsize=(70,70))
    plt.rc('xtick', labelsize=40) 
    plt.rc('ytick', labelsize=40) 
    return sns.heatmap(df.corr(method='spearman'), annot=True, square=True, cmap='coolwarm', annot_kws={'size': 10})

def correlation_1_vs_all(df, feature, threshold):
    pd.set_option('display.max_rows', None)
    df = df.corr().abs().unstack().sort_values(kind="quicksort", ascending=False).reset_index()
    df.rename(columns={"level_0": "Feature 1", "level_1": "Feature 2", 0: 'Correlation Coefficient'}, inplace=True)
    df = df.drop(df[df['Correlation Coefficient'] == 1.0].index)
    return df[(df['Feature 1'] == feature) & (df['Correlation Coefficient'] > threshold)]

def correlation_all_vs_all(df, threshold, target_feature):
    pd.set_option('display.max_rows', None)
    df_temp = df.corr().abs().unstack().sort_values(kind="quicksort", ascending=False).reset_index()
    df_temp.rename(columns={"level_0": "Feature 1", "level_1": "Feature 2", 0: 'Correlation Coefficient'}, inplace=True)
    df_temp.drop(df.iloc[1::2].index, inplace=True)
    df_temp = df_temp.drop(df_temp[df_temp['Correlation Coefficient'] == 1.0].index)
    lista_feature1= df_temp['Feature 1']
    lista_feature2= df_temp['Feature 2']
    lista_corr1=[]
    lista_corr2=[]
    for x in lista_feature1:
        lista_corr1.append(np.corrcoef(df[x],df[target_feature])[0][1])
    
    for x in lista_feature2:
        lista_corr2.append(np.corrcoef(df[x],df[target_feature])[0][1])
        
    df_temp['corr1_target']= lista_corr1
    df_temp['corr2_target']= lista_corr2

    return df_temp[df_temp['Correlation Coefficient'] > threshold]

def feature_selector(df, y, threshold_y, threshold_x):

    temp_features_list = correlation_1_vs_all(df, y, threshold_y)['Feature 2'].tolist() # take main variables
    chosen_features = []

    while len(temp_features_list) > 0:

        x = temp_features_list[0]
        chosen_features.append(x)
        temp_features_list.remove(x)
        temp_correlation_list = correlation_1_vs_all(df, x, threshold_x)['Feature 2'].tolist() # take main variables

        for x in temp_correlation_list:
            if x in temp_features_list:
                temp_features_list.remove(x)

    return chosen_features



In [82]:
final_df = pd.read_csv('data/multi_df.csv')

#final_df.to_csv('data/final_df.csv')
final_df.drop(['Unnamed: 0'],axis=1,inplace=True)

final_df

Date  opening_price  highest_price  lowest_price  closing_price  \
0     2013-07-17           97.1          100.0          96.2           98.5   
1     2013-07-18           98.5           98.8          86.2           90.1   
2     2013-07-19           90.1           95.2          87.6           92.0   
3     2013-07-20           92.0           93.1          89.3           89.8   
4     2013-07-21           89.8           92.0          88.0           92.0   
5     2013-07-22           92.0           92.0          89.8           91.6   
6     2013-07-23           91.6           97.1          91.6           95.6   
7     2013-07-24           95.6           96.0          92.3           95.1   
8     2013-07-25           95.1           97.5          93.6           96.9   
9     2013-07-26           96.9           97.5          96.0           96.0   
10    2013-07-27           96.0           97.0          93.0           94.4   
11    2013-07-28           94.4          100.6          94.0           98.8   
12    2013-07-29           98.8          102.8          98.4          101.5   
13    2013-07-30          101.5          108.0         100.5          108.0   
14    2013-07-31          108.0          111.7         103.6          106.2   
15    2013-08-01          106.2          108.0         103.0          104.0   
16    2013-08-02          104.0          108.0         101.2          104.5   
17    2013-08-03          104.5          105.9         102.0          104.9   
18    2013-08-04          104.9          106.0         103.5          105.1   
19    2013-08-05          105.1          107.8         105.0          106.7   
20    2013-08-06          106.7          107.5         105.1          106.6   
21    2013-08-07          106.6          107.0         105.2          106.0   
22    2013-08-08          106.0          106.7         101.0          103.1   
23    2013-08-09          103.1          105.8         101.9          102.8   
24    2013-08-10          102.8          103.9         102.4          103.0   
25    2013-08-11          103.0          105.2         102.7          105.0   
26    2013-08-12          105.0          108.1         103.5          106.8   
27    2013-08-13          106.8          109.6         104.5          109.6   
28    2013-08-14          109.6          115.0         108.0          112.6   
29    2013-08-15          112.6          113.3         108.8          110.0   
30    2013-08-16          110.0          112.3         108.2          109.0   
31    2013-08-17          109.0          114.0         108.2          112.8   
32    2013-08-18          112.8          114.7         112.0          113.4   
33    2013-08-19          113.4          123.8         111.8          118.5   
34    2013-08-20          118.5          123.0         116.8          121.2   
35    2013-08-21          121.2          125.0         119.7          123.3   
36    2013-08-22          123.3          124.5         120.5          122.0   
37    2013-08-23          122.0          122.0         118.4          118.5   
38    2013-08-24          118.5          121.4         118.0          119.6   
39    2013-08-25          119.6          123.0         119.1          122.1   
40    2013-08-26          122.1          123.0         119.9          120.1   
41    2013-08-27          120.1          133.0         120.0          131.3   
42    2013-08-28          131.3          131.7         128.0          128.8   
43    2013-08-29          128.8          131.2         128.2          129.3   
44    2013-08-30          129.3          142.8         128.6          138.0   
45    2013-08-31          138.0          148.7         135.9          141.0   
46    2013-09-01          141.0          147.3         141.0          146.0   
47    2013-09-02          146.0          148.5         142.1          144.0   
48    2013-09-03          144.0          148.9         142.2          144.0   
49    2013-09-04          144.0          145.8         130.1  

In [87]:
column_1 = final_df["FUTDXY"]
column_2 = final_df["next_day_closing_price"]
correlation = column_1.corr(column_2)

print(correlation)

0.05591806171633373


In [84]:
columnas=list(final_df.columns[1:64])

In [85]:
columnas

['opening_price',
 'highest_price',
 'lowest_price',
 'closing_price',
 'transactions_in_blockchain',
 'avg_block_size',
 'sent_by_adress',
 'avg_mining_difficulty',
 'avg_hashrate',
 'mining_profitability',
 'sent_coins_in_usd',
 'avg_transaction_fees',
 'median_transaction_fees',
 'avg_block_time',
 'avg_transaction_value',
 'median_transaction_value',
 'tweets_day',
 'google_trends',
 'active_addresses',
 'top100_to_total_percentage',
 'avg_fee_to_reward',
 'avg_price_usd',
 'market_cap_usd',
 'sf_ratio',
 'number_of_coins_in_circulation',
 'miner_revenue',
 'lbma_gold',
 'VIX_spot',
 'ETH_spot',
 'MSCIACW_spot',
 'WTI_spot',
 'FUTMSCIACWI',
 'FUTWTI',
 'FUT500',
 'FUTGOLD',
 'FUTVIX',
 'FUTBTC',
 'FUTDXY',
 'SWAPBASIS',
 'FUTBASIS',
 'FUTALT',
 'SP500_spot',
 'DXY_spot',
 'BDM_spot',
 'bc_volatility',
 'ST_UTXOs',
 'tweets_positive_negative_ratio_adj',
 'telegram_positive_ratio_adj',
 'telegram_number',
 'large_holders_netflow',
 'in_out_ratio_adj',
 'profit_losses_ratio_adj',
 'ne

In [78]:
for x in tqdm(columnas):
    if x!='next_day_closing_price':
        globals()[str(x)+"_df"] = final_df[[x,'next_day_closing_price']]
        final_df.drop([x],inplace=True,axis=1)
        for y in final_df.columns:
            if x.split(" ")[0] == y.split(" ")[0]:
                globals()[str(x)+"_df"][y] = final_df[y]
                final_df.drop([y],inplace=True,axis=1)

100%|██████████████████████████████████████████████████████████████████████████████████| 63/63 [01:16<00:00,  1.21s/it]


In [79]:
# Cogemos las 2 principlaes variables que no esten correlacionadas entre ellas en mas de 0.9

for x in tqdm(columnas):
    if x!='next_day_closing_price':

        for y in feature_selector(globals()[(str(x)+"_df")], 'next_day_closing_price', 0,0.9)[0:2]:
            final_df[y] =  globals()[(str(x)+"_df")][y]


100%|██████████████████████████████████████████████████████████████████████████████████| 63/63 [01:16<00:00,  1.21s/it]


In [80]:
final_df

Date  next_day_closing_price  opening_price  \
0     2013-07-17                    90.1           97.1   
1     2013-07-18                    92.0           98.5   
2     2013-07-19                    89.8           90.1   
3     2013-07-20                    92.0           92.0   
4     2013-07-21                    91.6           89.8   
5     2013-07-22                    95.6           92.0   
6     2013-07-23                    95.1           91.6   
7     2013-07-24                    96.9           95.6   
8     2013-07-25                    96.0           95.1   
9     2013-07-26                    94.4           96.9   
10    2013-07-27                    98.8           96.0   
11    2013-07-28                   101.5           94.4   
12    2013-07-29                   108.0           98.8   
13    2013-07-30                   106.2          101.5   
14    2013-07-31                   104.0          108.0   
15    2013-08-01                   104.5          106.2   
16    2013-08-02                   104.9          104.0   
17    2013-08-03                   105.1          104.5   
18    2013-08-04                   106.7          104.9   
19    2013-08-05                   106.6          105.1   
20    2013-08-06                   106.0          106.7   
21    2013-08-07                   103.1          106.6   
22    2013-08-08                   102.8          106.0   
23    2013-08-09                   103.0          103.1   
24    2013-08-10                   105.0          102.8   
25    2013-08-11                   106.8          103.0   
26    2013-08-12                   109.6          105.0   
27    2013-08-13                   112.6          106.8   
28    2013-08-14                   110.0          109.6   
29    2013-08-15                   109.0          112.6   
30    2013-08-16                   112.8          110.0   
31    2013-08-17                   113.4          109.0   
32    2013-08-18                   118.5          112.8   
33    2013-08-19                   121.2          113.4   
34    2013-08-20                   123.3          118.5   
35    2013-08-21                   122.0          121.2   
36    2013-08-22                   118.5          123.3   
37    2013-08-23                   119.6          122.0   
38    2013-08-24                   122.1          118.5   
39    2013-08-25                   120.1          119.6   
40    2013-08-26                   131.3          122.1   
41    2013-08-27                   128.8          120.1   
42    2013-08-28                   129.3          131.3   
43    2013-08-29                   138.0          128.8   
44    2013-08-30                   141.0          129.3   
45    2013-08-31                   146.0          138.0   
46    2013-09-01                   144.0          141.0   
47    2013-09-02                   144.0          146.0   
48    2013-09-03                   132.5          144.0   
49    2013-09-04                   130.2          144.0   
50    2013-09-05                   121.9          132.5   
51    2013-09-06                   129.0          130.2   
52    2013-09-07                   126.3          121.9   
53    2013-09-08                   133.1          129.0   
54    2013-09-09                   132.6          126.3   
55    2013-09-10                   142.1          133.1   
56    2013-09-11                   139.4          132.6   
57    2013-09-12                   140.7          142.1   
58    2013-09-13                   136.7          139.4   
59    2013-09-14                   138.3          140.7   
60    2013-09-15                   139.4          136.7   
61    2013-09-16                   139.1          138.3   
62    2013-09-17                   140.4          139.4   
63    2013-09-18                   135.1          139.1   
64    2013-09-19                   133.8          140.4   
65    2013-09-20                   134.4          135.1   
66    2013-09-21                   134.0          133.8   


In [81]:
final_df.to_csv('data/2_de_cada.csv')

In [58]:
## Para futuro mirar correlaciones negativas DXY